In [26]:
import pandas as pd 

def csv_codif(file_path, encodings = ['utf-8', 'latin1', 'ISO-8859-1', 'cp1252']):
    for encoding in encodings:
        try:
            df = pd.read_csv(file_path, encoding = encoding)
            return df
        except UnicodeDecodeError:
            pass
    return None
file_path = 'E://files_pandas//datos_abiertos//IRS_localidad_2020.csv'
df_derhab = csv_codif(file_path)
df_derhab = df_derhab[df_derhab['ent'] == 'Hidalgo']
columnas = ['mun','i_sdsalud']
df_derhab = df_derhab[columnas]
df_derhab_prom = df_derhab.groupby('mun')['i_sdsalud'].mean().reset_index()
df_derhab_prom = df_derhab_prom.sort_values('i_sdsalud', ascending = False)
df_derhab_prom['i_sdsalud'] = df_derhab_prom['i_sdsalud'].round(2)

import geopandas as gpd
import folium

# Ruta al archivo SHP o GeoJSON
try:
    gdf = gpd.read_file("E://files_pandas//sisver//muni_2018gw//muni_2018gw.shp", encoding='utf-8')
except UnicodeDecodeError:
    gdf = gpd.read_file("E://files_pandas//sisver//muni_2018gw//muni_2018gw.shp", encoding='latin-1')

# Leer el archivo SHP
gdf = gdf[gdf['NOM_ENT'] == 'Hidalgo']
# Crear el mapa base centrado en Hidalgo
m = folium.Map(location=[20.0911, -98.7624], zoom_start=8)  # Coordenadas aproximadas de Hidalgo

# Crear un GeoDataFrame con los datos de promedio_analf
gdf = gdf.merge(df_derhab_prom, left_on='NOM_MUN', right_on='mun')

# Crear el Choropleth
folium.Choropleth(
    geo_data=gdf,
    name='choropleth',
    data=gdf,
    columns=['mun', 'i_sdsalud'],
    key_on='feature.properties.NOM_MUN',
    fill_color='GnBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Población sin derechohabiencia a servicios de salud'
).add_to(m)

# Agregar capas de control
folium.LayerControl().add_to(m)

# Guardar el mapa en un archivo HTML
m.save('E://files_pandas//sisver//mapa_derechohabiencia_hidalgo.html')

# Mostrar el mapa
m